Expected input is a pyspark dataframe with a column containing image as base64 string for input into VLMs

DICOM images are previously scaled down and converted into base64 string via `dbx.pixels.dicom.dicom_to_base64jpg`

In [6]:
# If running over databricks-connect.
# Skip this cell if running as Databricks NB
from databricks.connect import DatabricksSession
spark = DatabricksSession.builder.getOrCreate()

In [2]:
%pip install openai
#dbutils.library.restartPython()


[notice] A new release of pip is available: 23.2.1 -> 25.1.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [7]:
%reload_ext autoreload
%autoreload 2

## Load input dataframe with column containing the image as base64 string

In [8]:
df = spark.table("hls_radiology.tcia.midi_b_val_subset")
display(df)

DataFrame[SeriesInstanceUID: string, PatientID: string, BodyPartExamined: string, Collection: string, CollectionURI: string, DateReleased: string, FileSize: bigint, ImageCount: bigint, Manufacturer: string, ManufacturerModelName: string, Modality: string, ProtocolName: string, SeriesDate: string, SeriesDescription: string, SeriesNumber: bigint, SoftwareVersions: string, StudyDate: string, StudyDesc: string, StudyInstanceUID: string, ThirdPartyAnalysis: string, TimeStamp: string, PatientID_masked: string, series_id_masked: string, path_masked: string, pixel_hash_masked: string, path: string, series_id: string, pixel_hash: string, frame: string, is_identical: boolean, jpg_base64str: string, jpg_base64str_masked: string, is_different: boolean, has_phi: bigint]

## Run `VLMTransformer().transform(df)`

In [0]:
from dbx.pixels.dicom.dicom_vlm_phi_detector import VLMTransformer

vlm_transformer = VLMTransformer(endpoint="databricks-claude-3-7-sonnet", 
                                 temperature = 0.0,
                                 num_output_tokens=200,
                                 inputCol="path", 
                                 outputCol="response")
out_df = vlm_transformer.transform(df.limit(3))
display(out_df)

## Run on a single image

In [ ]:
from dbx.pixels.dicom.dicom_vlm_phi_detector import VLMPhiExtractor
from dbx.pixels.dicom.dicom_utils import remove_dbfs_prefix

# Get single dicom file
path = df.select("path").take(1)[-1]['path']
extractor = VLMPhiExtractor(endpoint="databricks-claude-3-7-sonnet")
extractor.extract(path)

25/06/05 17:13:17 ERROR [PIXELS] dbx.pixels: Error converting dicom to image: [Errno 2] No such file or directory: '/Volumes/hls_radiology/tcia/downloads/unzipped/2.1.656.0.2.8048482.9.537.1658163530109825238/1-1.dcm'


(None,
 0,
 0,
 0,
 "[Errno 2] No such file or directory: '/Volumes/hls_radiology/tcia/downloads/unzipped/2.1.656.0.2.8048482.9.537.1658163530109825238/1-1.dcm'")